# GDP growth outcomes, outbreak severity, containment stringency, and mobility

## 1. Import libraries

In [52]:
# Import pandas, matplotlib, seaborn, numpy, plotly, sklearn and datetime
import pandas as pd
import plotly_express as px
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
from matplotlib import pyplot as plt
import seaborn as sns
import numpy as np
from sklearn import preprocessing
import datetime as dt
from pandasgui import show


## 2. GDP growth

In [53]:
# Read GDP data (updatable--just refresh CEIC link)
df_gdp = pd.read_excel('GDP_yoy_global.xlsx', sheet_name='for-python')
# Drop countries with no GDP data for all periods
df_gdp.dropna(axis=0, how='all', subset=['gdp2019q4', 'gdp2020q1', 'gdp2020q2'], inplace=True)

In [54]:
#Generate summary statistics
df_gdp.describe().style.format('{:.1f}')

In [55]:
# Create an interactive box plot to see the distribution of GDP growth outcomes
fig = px.box(data_frame=df_gdp,
             y=['gdp2019q4', 'gdp2020q1', 'gdp2020q2'],
             hover_name='country',
             hover_data={'variable': False,
                         'value': ':.1f'},
             labels={'value': 'GDP growth (%)'},
             template='plotly_white',
             points='outliers',
             notched=True,
             title='Distribution of GDP growth outcomes, 2019Q4-2020Q2')
fig.update_layout({'xaxis': {'title': '',
                             'showgrid': False, 
                             'tickmode': 'array',
                             'tickvals': ['gdp2019q4', 'gdp2020q1', 'gdp2020q2'],
                             'ticktext': ['2019Q4', '2020Q1', '2020Q2']},
                   'yaxis': {'title': 'y-o-y % change',
                             'showgrid': False,
                             'nticks': 6}})
fig.show()

In [56]:
# Convert wide to long panel
df_gdp_long = pd.melt(df_gdp, id_vars='code', 
                      value_vars=['gdp2019q4', 'gdp2020q1', 'gdp2020q2'],
                      var_name='period', value_name='gdp_growth')
df_gdp_long.loc[:, 'period'].replace({'gdp2019q4': '2019Q4',
                                      'gdp2020q1': '2020Q1',
                                      'gdp2020q2': '2020Q2'}, inplace=True)
# Create an interactive distribution plot
fig = px.histogram(data_frame=df_gdp_long,
                   x='gdp_growth',
                   color='period',
                   hover_data={'gdp_growth': ':.1f'},
                   labels={'period': 'Period',
                           'gdp_growth': 'GDP growth (%)'},
#                  marginal='rug',
                   opacity=0.75,
                   barmode='overlay',
#                  range_x=[-70, 70],
                   title='Distribution of GDP growth outcomes, 2019Q4-2020Q2',
                   template='plotly_white')
fig.update_layout({'xaxis': {'title': 'y-o-y % change',
                             'showgrid': False, 
                             'tickmode': 'array',
                             'zeroline': False},
                   'yaxis': {'title': 'Frequency',
                             'showgrid': False,
                             'nticks': 6},
                   'legend': {'title': 'Period'}})
fig.show()

In [57]:
# Create a data frame containing top n and worst n countries
n = 15
df_gdp_2020q1 = df_gdp.dropna(subset=['gdp2020q1']).sort_values(by='gdp2020q1')[['country', 'code', 'gdp2020q1']]
df_gdp2020q1_top = df_gdp_2020q1.head(n)
df_gdp2020q1_worst = df_gdp_2020q1.tail(n)
df_gdp_2020q1_tw = df_gdp2020q1_top.append(df_gdp2020q1_worst)
# Plot interactive horizontal bar
fig = px.bar(data_frame=df_gdp_2020q1_tw,
             x='gdp2020q1', y='country',
             color='gdp2020q1',
             hover_name='country',
             hover_data={'country': False,
                         'gdp2020q1': ':.1f'},
             text='country',
             labels={'gdp2020q1': 'GDP growth<br>(y-o-y % change)'},
             title=f'GDP growth rates in 2020Q1:<br>Top {n} and Worst {n}',
             template='plotly_white',
             height=700)
fig.update_layout({'yaxis': {'title': '',
                             'visible': False},
                   'xaxis': {'range': [-80, 80], 'showgrid': False, 'visible': False},
                   'coloraxis': {'colorbar': {'lenmode': 'fraction',
                                              'len': 0.5,
                                              'thickness': 10}}})
fig.update_traces(textposition='outside')
fig.show()
# Hide annoying warnings hehe
import warnings
warnings.filterwarnings('ignore')

In [58]:
# Create a data frame containing top n and worst n countries
n = 15
df_gdp_2020q2 = df_gdp.dropna(subset=['gdp2020q2']).sort_values(by='gdp2020q2')[['country', 'code', 'gdp2020q2']]
df_gdp2020q2_top = df_gdp_2020q2.head(n)
df_gdp2020q2_worst = df_gdp_2020q2.tail(n)
df_gdp_2020q2_tw = df_gdp2020q2_top.append(df_gdp2020q2_worst)
fig = px.bar(data_frame=df_gdp_2020q2_tw,
             x='gdp2020q2', y='country',
             color='gdp2020q2',
             hover_name='country',
             hover_data={'country': False,
                         'gdp2020q2': ':.1f'},
             text='country',
             labels={'gdp2020q2': 'GDP growth<br>(y-o-y % change)'},
             title=f'GDP growth rates in 2020Q2:<br>Top {n} and Worst {n}',
             template='plotly_white',
             height=700)
fig.update_layout({'yaxis': {'title': '',
                             'visible': False},
                   'xaxis': {'range': [-110, 110], 'showgrid': False, 'visible': False},
                   'coloraxis': {'colorbar': {'lenmode': 'fraction',
                                              'len': 0.5,
                                              'thickness': 10}}})
fig.update_traces(textposition='outside')
fig.show()

In [59]:
# Assign new columns for GDP growth declines
df_gdp = df_gdp.assign(gdp_decline_q1 = lambda x: x.gdp2020q1 - x.gdp2019q4,
                       gdp_decline_q2q4 = lambda x: x.gdp2020q2 - x.gdp2019q4,
                       gdp_decline_q2q1 = lambda x: x.gdp2020q2 - x.gdp2020q1)
# Generate summary statistics
df_gdp.iloc[:, 5:].describe()

gdp_decline_q1  gdp_decline_q2q4  gdp_decline_q2q1
count       98.000000         89.000000         89.000000
mean        -2.887681        -14.130186        -11.181342
std          4.729078          8.726117          7.093252
min        -42.725478        -62.631207        -38.882528
25%         -3.536010        -17.602316        -14.344822
50%         -1.999551        -12.249536        -10.100000
75%         -0.954614         -9.652161         -7.672189
max          2.428152          0.670320         10.000000

In [60]:
# Convert wide to long panel
df_gdp_long = pd.melt(df_gdp, id_vars='code', 
                      value_vars=['gdp_decline_q1', 'gdp_decline_q2q4', 'gdp_decline_q2q1'],
                      var_name='period', value_name='gdp_growth_declines')
df_gdp_long.loc[:, 'period'].replace({'gdp_decline_q1': '2020Q1',
                                      'gdp_decline_q2q4': '2020Q2 (from 2019Q4)',
                                      'gdp_decline_q2q1': '2020Q2 (from 2020Q1)'}, inplace=True)
# Create an interactive distribution plot
fig = px.histogram(data_frame=df_gdp_long,
                   x='gdp_growth_declines',
                   color='period',
                   hover_data={'gdp_growth_declines': ':.1f'},
                   labels={'period': 'Period',
                           'gdp_growth_declines': 'GDP growth decline (pp)'},
#                  marginal='rug',
                   opacity=0.75,
                   barmode='overlay',
#                  range_x=[-70, 70],
                   title='Distribution of GDP growth declines in 2020:<br>Relative to 2019Q4 or 2020Q1',
                   template='plotly_white')
fig.update_layout({'xaxis': {'title': 'percentage points',
                             'showgrid': False, 
                             'tickmode': 'array',
                             'zeroline': False},
                   'yaxis': {'title': 'Frequency',
                             'showgrid': False,
                             'nticks': 6},
                   'legend': {'title': 'Period'}})
fig.show()

In [61]:
# Convert wide to long panel
df_gdp_long = pd.melt(df_gdp, id_vars='code', 
                      value_vars=['gdp_decline_q1', 'gdp_decline_q2q4'],
                      var_name='period', value_name='gdp_growth_declines')
df_gdp_long.loc[:, 'period'].replace({'gdp_decline_q1': '2020Q1',
                                      'gdp_decline_q2q4': '2020Q2'}, inplace=True)
# Create an interactive distribution plot
fig = px.histogram(data_frame=df_gdp_long,
                   x='gdp_growth_declines',
                   color='period',
                   hover_data={'gdp_growth_declines': ':.1f'},
                   labels={'period': 'Period',
                           'gdp_growth_declines': 'GDP growth decline (pp)'},
#                  marginal='rug',
                   opacity=0.75,
                   barmode='overlay',
#                  histnorm='probability density',
#                  range_x=[-70, 70],
                   title='Distribution of GDP growth declines in 2020 from pre-COVID period',
                   template='plotly_white')
fig.update_layout({'xaxis': {'title': 'percentage points',
                             'showgrid': False, 
                             'tickmode': 'array',
                             'zeroline': False},
                   'yaxis': {'title': 'Frequency',
                             'showgrid': False,
                             'nticks': 6},
                   'legend': {'title': 'Period'}})
fig.show()

## 3. OxCGRT data

In [62]:
# Import the Python libraries
import pandas as pd
import plotly.express as px
# Import the latest OxCGRT data from the team's Github repo
url_str = 'https://raw.githubusercontent.com/OxCGRT/covid-policy-tracker/master/data/OxCGRT_latest.csv'
df_str = pd.read_csv(url_str, parse_dates=['Date'])
# Let's focus on country aggregates and drop the subregional data (US and UK states)
df_str = df_str[df_str['RegionCode'].isnull()]

In [63]:
# Create a list of ADB DMCs
dmc = ['Azerbaijan', 'Georgia', 'Kazakhstan', 'Kyrgyz Republic', 'Tajikistan', 'Turkmenistan',
       'Uzbekistan', 'China', 'Hong Kong', 'Mongolia', 'South Korea', 'Taiwan', 'Afghanistan', 
       'Bangladesh', 'Bhutan', 'India', 'Nepal', 'Pakistan', 'Sri Lanka', 'Brunei', 'Cambodia', 
       'Indonesia', 'Laos', 'Malaysia', 'Myanmar', 'Philippines', 'Singapore', 'Thailand', 
       'Timor-Leste', 'Vietnam', 'Fiji', 'Papua New Guinea', 'Solomon Islands', 'Vanuatu']

# Create a dataframe of stringency for ADB DMCs and export this to Excel
df_str.loc[df_str['CountryName'].isin(dmc), ['CountryName', 'Date', 'StringencyIndex']].\
pivot(index='CountryName', columns='Date', values='StringencyIndex').\
to_excel(f'stringency-{str(dt.date.today().month) + str(dt.date.today().day)}.xlsx')

In [64]:
# Make a list of countries to display in the line plot
outbreak_countries = ['China', 'South Korea', 'United States', 'France', 'United Kingdom', 'Italy']
herd_1 = ['Italy', 'Albania', 'Denmark', 'Norway', 'Spain', 'Slovenia', 'Turkey', 'Germany', 'United Kingdom']
herd_2 = ['Paraguay', 'Peru', 'Bolivia', 'Brazil', 'Argentina', 'Mexico']
herd_3 = ['Iraq', 'Saudi Arabia', 'Lebanon', 'Iran', 'Yemen']
herd_4 = ['Indonesia', 'Malaysia', 'Philippines', 'Singapore', 'Thailand', 'Vietnam']
herd_5 = ['Kenya', 'Rwanda', 'Cameroon', 'South Africa', 'Cote d’Ivoire', 'South Sudan', 'Somalia',
          'Zimbabwe', 'Ethiopia', 'Benin', 'Nigeria', 'Tanzania', 'Burundi']
# Create an interactive line plot
fig = px.line(df_str[df_str['CountryName'].isin(outbreak_countries)], 
              x='Date', y='StringencyIndex',
              color='CountryName',
#               facet_row='Herd',
#               facet_row_spacing=0.05,
#               category_orders={'Herd': ['Europe', 'Middle East', 'Latin America', 
#                                         'Southeast Asia', 'Sub-Saharan Africa']},
              labels={'StringencyIndex': '',
                      'Herd': ''},
              range_y=[0, 100],
              title='Stringency index for selected countries, January 2020 - present',
              template='plotly_white')
# fig.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1], textangle=360,
#                                            font={'size':9}))
# fig.for_each_trace(lambda t: t.update(showlegend=False))
fig.update_layout({'xaxis': {'title': '',
                             'showgrid': False},
                   'yaxis': {'title': 'Index, 0=No measure, 100=Strictest',
                             'showgrid': False}})
fig.show()

In [65]:
# Make a list of countries to display in the line plot
outbreak_countries = ['China', 'South Korea', 'United States', 'France', 'United Kingdom', 'Italy']
herd_1 = ['Italy', 'Albania', 'Denmark', 'Norway', 'Spain', 'Slovenia', 'Turkey', 'Germany', 'United Kingdom']
herd_2 = ['Paraguay', 'Peru', 'Bolivia', 'Brazil', 'Argentina', 'Mexico']
herd_3 = ['Iraq', 'Saudi Arabia', 'Lebanon', 'Iran', 'Yemen']
herd_4 = ['Indonesia', 'Malaysia', 'Philippines', 'Singapore', 'Thailand', 'Vietnam']
herd_5 = ['Kenya', 'Rwanda', 'Cameroon', 'South Africa', 'Cote d’Ivoire', 'South Sudan', 'Somalia',
          'Zimbabwe', 'Ethiopia', 'Benin', 'Nigeria', 'Tanzania', 'Burundi']
df_str['Herd'] = np.nan
df_str.loc[df_str['CountryName'].isin(herd_1), 'Herd'] = 'Europe'
df_str.loc[df_str['CountryName'].isin(herd_2), 'Herd'] = 'Latin America'
df_str.loc[df_str['CountryName'].isin(herd_3), 'Herd'] = 'Middle East'
df_str.loc[df_str['CountryName'].isin(herd_4), 'Herd'] = 'Southeast Asia'
df_str.loc[df_str['CountryName'].isin(herd_5), 'Herd'] = 'Sub-Saharan Africa'
df_str.dropna(subset=['Herd'], inplace=True)
# Create an interactive line plot
fig = px.line(df_str, 
              x='Date', y='StringencyIndex',
              color='CountryName',
              facet_row='Herd',
              facet_row_spacing=0.05,
              category_orders={'Herd': ['Europe', 'Middle East', 'Latin America', 
                                        'Southeast Asia', 'Sub-Saharan Africa']},
              labels={'StringencyIndex': '',
                      'Herd': ''},
              range_y=[0, 100],
              title='Stringency index for selected countries, January 2020 - present',
              template='plotly_white',
              height=900)
fig.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1], textangle=360,
                                           font={'size':9}))
fig.for_each_trace(lambda t: t.update(showlegend=False))
fig.update_layout({'xaxis': {'title': ''}})
fig.show()

In [66]:
# Create a data frame for the Philippines
df_str_ph = df_str.loc[df_str['CountryName']=='Philippines']
df_str_ph = df_str_ph[['CountryName', 'CountryCode', 'Date', 
                       'C1_School closing', 'C2_Workplace closing', 'C3_Cancel public events',
                       'C4_Restrictions on gatherings', 'C5_Close public transport', 
                       'C6_Stay at home requirements', 'C7_Restrictions on internal movement', 
                       'C8_International travel controls']]
df_str_ph.columns = ['CountryName', 'CountryCode', 'Date', 
                     'School closing', 'Workplace closing', 'Cancel public events',
                     'Restrictions on gatherings', 'Close public transport', 
                     'Stay at home requirements', 'Restrictions on internal movement', 
                     'International travel controls']

In [67]:
# Convert wide to long
df_str_ph_long = df_str_ph.melt(id_vars='Date',
                                value_vars=[
                                            'School closing', 
                                            'Workplace closing', 
                                            'Cancel public events', 
                                            'Restrictions on gatherings', 
                                            'Close public transport', 
                                            'Stay at home requirements',
                                            'Restrictions on internal movement', 
                                            'International travel controls'
                                            ],
                                var_name='Containment measure',
                                value_name='Score')
# Drop missing values
df_str_ph_long.dropna(inplace=True)
# Change the order of containment measures
sorter = [
          'International travel controls', 
          'Cancel public events', 
          'School closing', 
          'Workplace closing', 
          'Restrictions on gatherings', 
          'Close public transport', 
          'Stay at home requirements', 
          'Restrictions on internal movement'
         ]
df_str_ph_long['Containment measure'] = df_str_ph_long['Containment measure'].astype('category')
df_str_ph_long['Containment measure'].cat.set_categories(sorter, inplace=True)
df_str_ph_long.sort_values(by=['Date', 'Containment measure'], inplace=True)
# Convert Date column to string
df_str_ph_long['Date'] = df_str_ph_long['Date'].astype(str).str[:10]


In [68]:
# Create an interactive bar chart
fig = px.bar(data_frame=df_str_ph_long.loc[df_str_ph_long['Date']>='2020-01-30'],
             x='Containment measure', y='Score',
             color='Containment measure',
             animation_frame='Date',
             animation_group='Containment measure',
             range_y=[0, 3],
             title='Containment measures in the Philippines, January 2020 to Present:<br>(0=No measures; 3=Strictest)',
             template='plotly_white')
fig.update_layout({'xaxis': {'title': '',
                            'showgrid': False,
                            'showticklabels': False},
                   'yaxis': {'title': '',
                             'showgrid': False,
                             'zeroline': False,
                             'nticks': 4,
                             'showticklabels': False},
                   'legend': {'title': 'Containment measure'}})
# fig['layout'].pop('updatemenus')
fig.show()

## 4. Google mobility data

In [69]:
# Extract mobility data from Google API
df_mob = pd.read_csv('https://www.gstatic.com/covid19/mobility/Global_Mobility_Report.csv')

# Keep country aggreagates only and drop region-level data
df_mob = df_mob.loc[df_mob['sub_region_1'].isna()]
df_mob = df_mob.loc[df_mob['sub_region_2'].isna()]
df_mob = df_mob.loc[df_mob['metro_area'].isna()]

In [70]:
# Create a dataframe of mobility for ADB DMCs
df_mob = df_mob.loc[df_mob['country_region'].isin(dmc)]

# Create a new column for non-residential mobility average
df_mob = df_mob.assign(average_mob = lambda x: (x.retail_and_recreation_percent_change_from_baseline + \
                                       x.grocery_and_pharmacy_percent_change_from_baseline + \
                                       x.parks_percent_change_from_baseline + \
                                       x.transit_stations_percent_change_from_baseline + \
                                       x.workplaces_percent_change_from_baseline) / 5)

# Keep relevant columns only
df_mob = df_mob[['country_region', 'date', 'average_mob']]

# Export to excel
df_mob = df_mob.pivot(index='country_region', columns='date', values='average_mob')
df_mob.to_excel(f'mobility-{str(dt.date.today().month) + str(dt.date.today().day)}.xlsx')